# Linear Programming, Optimization
**Fundamental theorem of linear programming**
"... Any linear program either is infeasible, is unbounded, or has an optimal solution with a finite objective value. In each case, [the algorithm] SIMPLEX acts appropriately." I.e. simplex will return an optimal solution or 'unbounded' or 'infeasible.' 
- *Introduction to Algorithms*, Third Edition, Cormen, Leirson, Rivest and Stein, 2009, MIT, Cambridge, Massachussetts, pg. 891

*Note:*
- "The Simplex algorithm does not run in polynomial time in the wors case, but it is fairly efficient and widely used in practice." (Ibid, 864)

😎 **In other words:** *If you can formulate a problem as a system of linear equations, and you have more than two variables (dimensions) then the simplex algorithm is probably your best bet to solving it.*

## Contents:
- pending completion

## Basic Example: Optimizing farming profit
Suppose a farmer has 240 acres of land. 
- they can farm corn for a profit of \$40/acre and time cost of 2hr/acre
- they can farm oats for a profit of \$30/acre and time cost of 1hr/acre
- they only have 320 farmable hours before harvest is due

How many acres of each should they plant to maximize profits?

### We formulate the word problem as a linear program

**Objective function:** profits `p = 40*c + 30*o`

subject to:

**Constraint 1:** `c + o <= 240` total acres farmed 

**Constraint 2:** `2c + o <= 320` total hours farmed

**Constraint 3:** `c, o >= 0` because they can't farm negative acres 

### We can graph the system of linear equations and constraints

In [30]:
import numpy as np
import pandas as pd
import plotly
import plotly.graph_objs as go

### Graph the solution space for the number of farmable acres

In [42]:
# notice the non-negativity constraint (i.e. constraint 3) is baked into the code here
acres = [a for a in range(0, 240)] 
    
acres_trace = go.Scatter(
    x = acres,
    # for y <= 240 - x
    y = [240 - a for a in acres], 
    fill = 'tozeroy',
    name = 'farmable acres; constraint 1'.title(),
    
)
data = [acres_trace]
layout = go.Layout(
    title = 'Feasible Solution Area',
    xaxis = {'title': 'acres of corn'},
    yaxis = {'title': 'acres of oats'},
    showlegend = True,
    legend = dict(
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    )
)
fig = go.Figure(data = data, layout = layout)
fig

**Constraint 1: `c + o <= 240` total acres farmed**
- The above graph visualizes the constraint relationship between acres farmed for corn and for oats.
- if you farm 240 acres of corn, you will have no acres left for oats and vice versa.

### We add the constraint of farmable hours

In [43]:
hours = [h for h in range(0, 320)]
hours_trace = go.Scatter(
    x = hours,
    # y <= 320 - 2x
    y = [320 - 2*h for h in hours if 320 - 2*h >= 0], 
        #we add the conditional to the list comprehension to satisfy the non-negativity constraint
    fill = 'tozeroy',
    name = 'farmable hours; constraint 2'.title(),
)

data = [acres_trace, hours_trace]
layout = go.Layout(
    title = 'Feasible Solution Area',
    xaxis = {'title': 'acres of corn'},
    yaxis = {'title': 'acres of oats'},
    showlegend = True,
    legend = dict(
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    )
)
fig = go.Figure(data = data, layout = layout)
fig

**Constraint 2:** `2c + o <= 320` total hours farmed
- the above graph shows the constrain relationship between hours farmed for corn and oats
- if you use all 320 hours farming corn you won't have any hours left to farm oats

Notice the intersection of the feasability spaces is a solution space to the system of equations resulting from combining both constraints

### Now we add the objective function (aka the profit function) to the system 
- `p = 40c + 30o` substitutting 
    - corn for `x` and 
    - oats for `y` 
- we can isolate `y` for a version of the familiar **y = mx + b** 
    - `p = 40x + 30y` --> `p - 40 = 30y` --> `y = (p/30) - (40/30)x` 



In [44]:
# declare constrained values of plantable corn acres
corn_acres = [a for a in range(240)]
# declare constrained values of plantable oats acres
oats_acres = [a for a in range(240)]
# profit as a 2D, 240x240 matrix with values p = 40c + 30o
# init the profit matrix as zeros
profit = np.zeros((240,240))

# for every possible number of corn acres planted
for i_corn in corn_acres:
    #for every possible number of oats acres planted
    for j_oat in oats_acres:
        # the profit at that combo; p = 40c + 30o
        profit[i_corn][j_oat] = 40*i_corn + 30*j_oat

In [46]:
fig.add_contour(
    # add the profit as a z value
    z = profit,
    colorscale = 'Greens',
    #contours_coloring = 'lines',
    #line_width = 2,
    name = 'Profit Margins',
    contours = dict(
        coloring = 'heatmap',
        showlabels = True,
        start = 0,
        end = np.max(profit),
        # 500 increments
        size = 500
    ),
)
fig

**The interactive plot gives us an intuitive sense of how to maximize the profit, given the constraints**
- we may have expected corn to be more profitable, but if you went "all in on corn." you'd run out of time after planting the 160th acre. 
- Not only is it more profitable to plant only oats, it also takes less time. You only have to plant for 240 hours, and you get to take the remaining time off.

## General Algorithmic Solution: `scipy.optimize.linprog`
- in general, you may have more than two constraints, more than two profit variables, etc. Anything beyond three dimensions won't be visualizable, but luckily math has a way to solve these functions for us.
- https://docs.scipy.org/doc/scipy/reference/generated/scipy.optimize.linprog.html


# Tinkering with 3d plots

In [64]:
# declare the figure
fig = go.Figure(
    # declare the data for the figure
    data = [
        # add the profit surface area
        go.Surface(
            # profit = 40*corn + 30*oats ; z = 40x + 30y
            z = profit,
            colorscale = 'Greens',
            opacity = 1,
        ),
    ]
)

fig

In [66]:
fig.add_scatter3d(
    x = corn_acres,
    y = [240 - a for a in acres], # for y <= 240 - x
    z = [12000 for c in corn_acres],
    mode = 'lines',
    surfaceaxis=2,
    surfacecolor = '#66c2a5',
    line=dict(
            color='black',
            width=4
        ),
)

In [67]:
# declare the figure
fig = go.Figure()

# add a trace
fig.add_trace(
    #add the profit surface area
    go.Surface(
        # profit = 40*corn + 30*oats ; z = 40x + 30y
        z = profit,
        colorscale = 'Greens',
        opacity = 1,
        name = 'Profit'
    )
)

# add a 3d mesh of farmable acres
fig.add_mesh3d(
    x=[240, 239.9, 0, 0],
    y=[0, 0, 240, 240.1],
    z=[0, 16000, 16000, 0],
    name = 'Farmable Acres',
)

fig

In [ ]:
go.Mesh3d(
            x=[0, 1, 2, 0],
            y=[0, 0, 1, 2],
            z=[0, 2, 0, 1],
        )

**add a trace to the 3d surface plot**

In [ ]:
fig.add_mesh3d(
    # add the x coordinates
    x = [240, 0, 240],
    # add the y coordinates
    y = [0, 240, 0],
    z = [0, 0, 5000],
    
)
fig

In [ ]:
fig.add_surface(
    x = corn_acres,
    y = [240 - a for a in corn_acres], # for y <= 240 - x
    z = 5000*np.ones((240,240))
)

In [ ]:
fig = go.Figure(
    data=[
        go.Mesh3d(
            x=[0, 1, 2, 0],
            y=[0, 0, 1, 2],
            z=[0, 2, 0, 1],
        )
    ], 
)

fig.show()

In [ ]:
fig = go.Figure(
    data=[
        go.Mesh3d(
            x=[0, 1, 2],
            y=[0, 0, 1],
            z=[0, 2, 0],
        )
    ], 
)

fig.show()

## Example Word Problem, Integer Programming:
### Capital Budgeting?
Suppose you need to buy as many notebooks as possible with a given budget ```n```. And notebooks are sold in "bundles" where each bundle has an integer quantity of books , ```q```, for an integer cost ```c```.

Input format:
1. n - an integer representing your budget
    - ex: 807
2. bundleQuantities - an array of length ```m``` of positive integers representing book quantities in each bundle
    - ex: [176,  98, 105,  65,  61,  30, 113,  60,  67,  80]
3. bundleCosts - an array of length ```m``` of positive integers representing book quantities in each bundle
    - ex: [194, 180,   1, 143, 131,  30,  73,  93,  55, 178]
    
#### Write a function buyBooks(n, bundleQuantities, bundleCosts) which returns an integer representing the maximum number of books you can buy.

Constraints:
1. You can only buy whole numbers of bundles
2. You can't buy "negative" bundles
3. 0< n, m, q, b <= cap



In [ ]:
import pandas as pd

In [ ]:
import numpy as np

## initialize values

In [ ]:
# set random seed for reproducible results
np.random.seed(seed = 57)

In [ ]:
# generate budget, and array lengths
cap = 1000
n = np.random.randint(1, cap)
print('budget is: ', n)
m = np.random.randint(1, cap)
print('array length is: ', m)

In [ ]:
bundleQuantities = np.random.randint(1, cap, size = m)
bundleQuantities[0:10]

In [ ]:
bundleCosts = np.random.randint(1,cap, size = m)
bundleCosts[0:10]

In [ ]:
books_purchasable = [int(n/bc)*bq for bc,bq in zip(bundleCosts, bundleQuantities)]
books_purchasable[0:10]

In [ ]:
max_books_purchased = max(books_purchasable)
max_books_purchased

In [ ]:
for i in range(len(books_purchasable)):
    if books_purchasable[i] == max(books_purchasable):
        ix = i
ix

In [ ]:
change_remaining = n - bundleCosts[ix]
change_remaining

In [ ]:
df = pd.DataFrame()
df['bdgt_1'] = [n for i in range(len(bundleCosts))]
df['bundle_qty'] = bundleQuantities
df['bundle_cst'] = bundleCosts
df['bks_per_dollar'] = df['bundle_qty']/df.bundle_cst
df['mx_bndls_1'] = (df.bdgt_1/df.bundle_cst).apply(int)
df['mx_books1'] = df.mx_bndls_1*df.bundle_qty
df['exp_1'] = df.mx_bndls_1*df.bundle_cst
df['bdgt_2'] = df.bdgt_1 - df.exp_1
df.head()

## naive maximization attempt
Using greedy stepwise decisions

In [ ]:
def maximizeBooksStepwise(n, bq, bc, verbose = False):
    '''Takes integer n, two integer arrays: bundleQuantities and 
    bundleCosts respectively (both of which are length m) and returns 
    integer sum of the max books purchasable at every iteration.
    Note: This algorithm does not guarantee an optimal solution.
    Ex: n = 510, bq = [500, 498, 3], bc = [500, 499, 12] has an optimal solution:
    bq[1]+bq[2] > bq[0]
    498 + 3 > 500
    but maximizeBooksStepwise returns the solution
    500. See algorithms on integer linear programming'''
    books_purchased = 0
    iteration = 0
    while n >= min(bc): #while we can afford any of the packages #O(m)
        bp = [int(n/c)*q for c,q in zip(bc, bq)] # max books purchasable for every bundle #O(m)
        mbp = max(bp) #O(m)
        if verbose:
            iteration += 1
            print(iteration, 'books_purchasable: ', bp[0:5], '...', bp[-5:])
        if verbose:
            print(iteration, 'purchased ', mbp, ' books')
        books_purchased += mbp
        if verbose:
            print(iteration, 'for a running total of: ', books_purchased)
        for i in range(len(bp)):
            if bp[i] == mbp: #retrieve the index of max books purchasable at this iteration #O(m)
                j = i
                break
        n = n - bc[j]*int(n/bc[j]) #adjust remaining budget
        if verbose:
            print(iteration, n, ' budget remaining')
            print('-----------------------------')
    return books_purchased

In [ ]:
# generate budget, and array lengths
cap = 10000
n = np.random.randint(cap, 2*cap)
print('budget is: ', n)
m = np.random.randint(1, cap)
print('array length is: ', m)
bundleQuantities = np.random.randint(1, cap, size = m)
print('bundleQuantities[0:5]', bundleQuantities[:5])
bundleCosts = np.random.randint(1,cap, size = m)
print('bundleCosts[0:5]', bundleCosts[:5])
print('')
maximizeBooksStepwise(n, bundleQuantities, bundleCosts, verbose = True)

## Using scipy.optimize.linprog()
Non integral implementation

In [ ]:
from scipy.optimize import linprog

In [ ]:
c = [-q/c for q,c in zip(bundleQuantities, bundleCosts)] # books/dolar coefficients
    #notice we have negated the values in c because linprog minimizes the given objective function
A = [bundleCosts] 
b = n # sum of Ax must be <= budget, n

res = linprog(c, A_ub = A, b_ub = b, options = {"disp": True})
print(res)

###### **The Problem** is that scipy.optimize is using non-integral optimization. It's purchasing fractions of bundles (which is not allowed). So of course it can always outperform maximizeBooksStepwise
- in essence: simplex is solving a different linear program than the one I am trying to solve

According to wikipedia, we can not rely on the total unimodularity guarantee for the simplex algorithm. Since the c vector we're using isn't integral but also because A isn't totally unimodular.

## I'll need to use an algorithm for Integer Linear Programming